In [1]:
import pandas as pd
import numpy as np
import folium
from folium.plugins import MarkerCluster
import plotly.express as px
from geopy.geocoders import Nominatim

pd.options.display.float_format = '{:.2f}'.format
pd.set_option('display.max_columns', None)

In [2]:
data = pd.read_csv('kc_house_data.csv')

In [3]:
df = data.copy()

In [4]:
df.head()

id             date     price  bedrooms  bathrooms  sqft_living  \
0  7129300520  20141013T000000 221900.00         3       1.00         1180   
1  6414100192  20141209T000000 538000.00         3       2.25         2570   
2  5631500400  20150225T000000 180000.00         2       1.00          770   
3  2487200875  20141209T000000 604000.00         4       3.00         1960   
4  1954400510  20150218T000000 510000.00         3       2.00         1680   

   sqft_lot  floors  waterfront  view  condition  grade  sqft_above  \
0      5650    1.00           0     0          3      7        1180   
1      7242    2.00           0     0          3      7        2170   
2     10000    1.00           0     0          3      6         770   
3      5000    1.00           0     0          5      7        1050   
4      8080    1.00           0     0          3      8        1680   

   sqft_basement  yr_built  yr_renovated  zipcode   lat    long  \
0              0      1955             0    98178 47.51 -122.26   
1            400      1951          1991    98125 47.72 -122.32   
2              0      1933             0    98028 47.74 -122.23   
3            910      1965             0    98136 47.52 -122.39   
4              0      1987             0    98074 47.62 -122.05   

   sqft_living15  sqft_lot15  
0           1340        5650  
1           1690        7639  
2           2720        8062  
3           1360        5000  
4           1800        7503

In [5]:
print(df.shape)
print('_'*30)
print(df.dtypes)

(21613, 21)
______________________________
id                 int64
date              object
price            float64
bedrooms           int64
bathrooms        float64
sqft_living        int64
sqft_lot           int64
floors           float64
waterfront         int64
view               int64
condition          int64
grade              int64
sqft_above         int64
sqft_basement      int64
yr_built           int64
yr_renovated       int64
zipcode            int64
lat              float64
long             float64
sqft_living15      int64
sqft_lot15         int64
dtype: object


In [6]:
df.isnull().sum()

id               0
date             0
price            0
bedrooms         0
bathrooms        0
sqft_living      0
sqft_lot         0
floors           0
waterfront       0
view             0
condition        0
grade            0
sqft_above       0
sqft_basement    0
yr_built         0
yr_renovated     0
zipcode          0
lat              0
long             0
sqft_living15    0
sqft_lot15       0
dtype: int64

## Perguntas de negócio

1. Qual a média do preço de compra dos imóveis por nível.
    - 0 -> 0 / 321.950
    - 1 -> 321.950 / 450.000
    - 2 -> 450.000 / 645.000
    - 3 -> + 645.000

2. Qual a média do tamanho da sala de estar dos imóveis(em M2) por 'size'.
    - 0 -> 0 / 132
    - 1 -> 132 / 177
    - 2 -> 177 / 236
    - 3 -> + 236

3. Adc as seguintes informações:
    - Place ID: identificador de localização
    - OSM: Type: Open Street Map type
    - Country: Nome do país
    - Country Code: Código do País

4. Adicione os seguintes filtros no mapa:
    - Tamanho minimo da area da sala de estar
    - Numero minimo de banheiros
    - Valor máximo de preço
    - Tamanho maximo da área do porão
    - Filtro das condições do imóvel
    - Filtro por ano de construção

5. Adicione os seguintes filtros no Dashboard:
    - Filtro por data disponível para compra
    - Filtro por ano de renovação.
    - Filtro se possui vista para a agua ou não

In [7]:
#TRATAMENTO DE DADOS

#renomeando coluna de notas
df.rename(columns={'grade': 'ratings'}, inplace=True)

#convertendo obj em data
df['date'] = pd.to_datetime(df['date'], format='%Y%m%dT000000')

#convertendo sqft - M²
df['m2_living'] = np.round(df['sqft_living'].apply(lambda x: x * 0.0929))
df['m2_lot'] = np.round(df['sqft_lot'].apply(lambda x: x * 0.0929))

#arredondando quantidade de banheiros
df['bathrooms'] = np.round(df['bathrooms'])

#criando colunas para codificar
#preço
df['price_code'] = df['price'].apply(lambda x: 0 if x < 321950 else
                                            1 if x < 450000 else
                                            2 if x < 645000 else 3)

#area útil 
df['m2_code'] = df['m2_living'].apply(lambda x: 0 if x < 132 else
                                            1 if x < 177 else
                                            2 if x < 236 else 3)

#vista para a agua
df['waterfront'] = df['waterfront'].apply(lambda x: 'Sim' if x == 1 else 'Nao')
#vista
df['view'] = df['view'].apply(lambda x: 'Sim' if x == 1 else 'Nao')

#transformando colunas em int
df['bathrooms'] = df['bathrooms'].astype(int)
df['floors'] = df['floors'].astype(int)

# Perguntas de negócios

In [8]:
df['id'].count()

21613

In [9]:
len(df[df['yr_renovated'] != 0])

914

In [10]:
df['price'].max()

7700000.0

In [11]:
df['price'].min()

75000.0

In [12]:
df.head()

id       date     price  bedrooms  bathrooms  sqft_living  \
0  7129300520 2014-10-13 221900.00         3          1         1180   
1  6414100192 2014-12-09 538000.00         3          2         2570   
2  5631500400 2015-02-25 180000.00         2          1          770   
3  2487200875 2014-12-09 604000.00         4          3         1960   
4  1954400510 2015-02-18 510000.00         3          2         1680   

   sqft_lot  floors waterfront view  condition  ratings  sqft_above  \
0      5650       1        Nao  Nao          3        7        1180   
1      7242       2        Nao  Nao          3        7        2170   
2     10000       1        Nao  Nao          3        6         770   
3      5000       1        Nao  Nao          5        7        1050   
4      8080       1        Nao  Nao          3        8        1680   

   sqft_basement  yr_built  yr_renovated  zipcode   lat    long  \
0              0      1955             0    98178 47.51 -122.26   
1            400      1951          1991    98125 47.72 -122.32   
2              0      1933             0    98028 47.74 -122.23   
3            910      1965             0    98136 47.52 -122.39   
4              0      1987             0    98074 47.62 -122.05   

   sqft_living15  sqft_lot15  m2_living  m2_lot  price_code  m2_code  
0           1340        5650     110.00  525.00           0        0  
1           1690        7639     239.00  673.00           2        3  
2           2720        8062      72.00  929.00           0        0  
3           1360        5000     182.00  464.00           2        2  
4           1800        7503     156.00  751.00           2        1

In [13]:
#influencia do ano de construção nos preços das casas
df_aux = np.round(df.loc[:, ['price', 'yr_built']].groupby('yr_built').mean().reset_index())
px.line(df_aux, x='yr_built', y='price')

In [14]:
#preço médio por condiçoes
df[['condition', 'price']].groupby('condition').mean().reset_index()

condition     price
0          1 334431.67
1          2 327287.15
2          3 542012.58
3          4 521200.39
4          5 612418.09

In [15]:
#preço médio por m2 code
df[['m2_code', 'price']].groupby('m2_code').mean().reset_index()

m2_code     price
0        0 338365.39
1        1 419465.60
2        2 517875.83
3        3 873596.52

In [16]:
#preco medio por quantidade de quarto
df[['bedrooms', 'price']].groupby('bedrooms').mean().reset_index()

bedrooms      price
0          0  409503.85
1          1  317642.88
2          2  401372.68
3          3  466232.08
4          4  635419.50
5          5  786599.83
6          6  825520.64
7          7  951184.66
8          8 1105076.92
9          9  893999.83
10        10  819333.33
11        11  520000.00
12        33  640000.00

In [17]:
#preço medio por quantidade de banheiros
df[['bathrooms', 'price']].groupby('bathrooms').mean().reset_index()

bathrooms      price
0          0  387935.71
1          1  346707.17
2          2  500535.41
3          3  746869.72
4          4 1076701.43
5          5 1846607.37
6          6 2603370.42
7          7 2734000.00
8          8 4328750.00

In [18]:
#top 5 imoveis mais caros
df_aux = df.loc[:, ['id', 'price', 'bedrooms', 'bathrooms','waterfront', 'view', 'condition', 'ratings', 'm2_living']].sort_values(by='price', ascending=False).head(5)
df_aux

id      price  bedrooms  bathrooms waterfront view  condition  \
7252  6762700020 7700000.00         6          8        Nao  Nao          4   
3914  9808700762 7062500.00         5          4        Sim  Nao          3   
9254  9208900037 6885000.00         6          8        Nao  Nao          3   
4411  2470100110 5570000.00         5          6        Nao  Nao          3   
1448  8907500070 5350000.00         5          5        Nao  Nao          3   

      ratings  m2_living  
7252       13    1119.00  
3914       11     933.00  
9254       13     919.00  
4411       13     855.00  
1448       12     743.00

In [19]:
# top 5 imoveis mais baratos
df_aux = df.loc[:, ['id', 'price', 'bedrooms', 'bathrooms','waterfront', 'view', 'condition', 'ratings', 'm2_living']].sort_values(by='price', ascending=True).head(5)
df_aux

id    price  bedrooms  bathrooms waterfront view  condition  \
1149   3421079032 75000.00         1          0        Nao  Nao          3   
15293    40000362 78000.00         2          1        Nao  Nao          1   
465    8658300340 80000.00         1          1        Nao  Nao          2   
16198  3028200080 81000.00         2          1        Nao  Nao          1   
8274   3883800011 82000.00         3          1        Nao  Nao          3   

       ratings  m2_living  
1149         3      62.00  
15293        5      72.00  
465          4      40.00  
16198        5      68.00  
8274         6      80.00

In [20]:
#casas com maiores notas sâo mais caras?
df_aux = df[['ratings', 'price']].groupby('ratings').mean().reset_index()
px.line(df_aux, x='ratings', y='price')

In [21]:
#preço de compra mais alto por numero de quartos
df_aux = df[['bedrooms', 'price']].groupby('bedrooms').max().reset_index()
px.bar(df_aux, x='bedrooms', y='price')

In [22]:
#tamanho médio de area de convicencia das casas aumentaram ao longo dos anos?
df_aux = df[['yr_built', 'm2_living']].groupby('yr_built').mean().reset_index()
px.line(df_aux, x='yr_built', y='m2_living')

In [23]:
#crescimento de preço de imóveis por ano, dia e mes

In [24]:
#Crescimento por ano
#Eixo x: Anos
#Eixo y: Soma dos preços
#Gráfico: barras

#first graph - YEAR
df['year'] = pd.to_datetime(df['date']).dt.year
df_aux = df[['price', 'year']].groupby('year').sum().reset_index()

px.bar(df_aux, x='year', y='price')

In [25]:
#second graph - DAY
df['day'] = pd.to_datetime(df['date'])
df_aux = df[['price', 'day']].groupby('day').mean().reset_index()

px.line(df_aux, x='day', y='price')

In [26]:
#third graph - Month
df['month'] = pd.to_datetime(df['date']).dt.strftime('%Y-%m')
df_aux = df[['price', 'month']].groupby('month').mean().reset_index()

px.line(df_aux, x='month', y='price')

In [27]:
df.head()

id       date     price  bedrooms  bathrooms  sqft_living  \
0  7129300520 2014-10-13 221900.00         3          1         1180   
1  6414100192 2014-12-09 538000.00         3          2         2570   
2  5631500400 2015-02-25 180000.00         2          1          770   
3  2487200875 2014-12-09 604000.00         4          3         1960   
4  1954400510 2015-02-18 510000.00         3          2         1680   

   sqft_lot  floors waterfront view  condition  ratings  sqft_above  \
0      5650       1        Nao  Nao          3        7        1180   
1      7242       2        Nao  Nao          3        7        2170   
2     10000       1        Nao  Nao          3        6         770   
3      5000       1        Nao  Nao          5        7        1050   
4      8080       1        Nao  Nao          3        8        1680   

   sqft_basement  yr_built  yr_renovated  zipcode   lat    long  \
0              0      1955             0    98178 47.51 -122.26   
1            400      1951          1991    98125 47.72 -122.32   
2              0      1933             0    98028 47.74 -122.23   
3            910      1965             0    98136 47.52 -122.39   
4              0      1987             0    98074 47.62 -122.05   

   sqft_living15  sqft_lot15  m2_living  m2_lot  price_code  m2_code  year  \
0           1340        5650     110.00  525.00           0        0  2014   
1           1690        7639     239.00  673.00           2        3  2014   
2           2720        8062      72.00  929.00           0        0  2015   
3           1360        5000     182.00  464.00           2        2  2014   
4           1800        7503     156.00  751.00           2        1  2015   

         day    month  
0 2014-10-13  2014-10  
1 2014-12-09  2014-12  
2 2015-02-25  2015-02  
3 2014-12-09  2014-12  
4 2015-02-18  2015-02

# mapa

In [28]:
#configurações gerais do mapa
map = folium.Map([ 47.608013 ,-122.335167],
            tiles='OpenStreetMap',
            zoom_start=9,
            width="%100",height="%100")

#adc coordenadas
coordenadas = df[['lat','long']]
folium.plugins.MarkerCluster(locations=coordenadas).add_to(map)
map